# Geomapping exploration

This notebook is an exploratory look at the methods I can use to overlay activity data from the Strava API onto a basemap

##  Strava API Setup

In [392]:
import json
import requests
import urllib3
import pandas as pd
import polyline
urllib3.disable_warnings(urllib3.exceptions.InsecureRequestWarning)

class StravaAPI():
    def __init__(self, codes_path):
        with open(codes_path, 'r') as f:
            self.codes = json.load(f) # TODO: NEED TO USE social_django.models.UserSocialAuth to get the Strava login for all users
        
    def get_user_data(self):
        auth_url = "https://www.strava.com/oauth/token"
        user_url = "https://www.strava.com/api/v3/athlete"


        # Get access token
        print("Requesting Token...\n")
        res = requests.post(auth_url, data=self.codes, verify=False)
        access_token = res.json()['access_token']
        print("Access Token = {}\n".format(access_token))

        # Get activity data
        header = {'Authorization': 'Bearer ' + access_token}
        activity_df_list = []
        for n in range(5):  # TODO: Change this to be higher
            param = {'per_page': 200, 'page': n+1}
            x = requests.get(user_url, headers = header, params = param).json
            print(pd.json_normalize(x))
            activities_json = requests.get(activites_url, headers=header, params=param).json()
            if not activities_json:
                break
            activity_df_list.append(pd.json_normalize(activities_json))
        activities_df = pd.concat(activity_df_list)
        print('Imported', len(activities_df),'activities')

        return user_data
    
    def get_activities(self):

        auth_url = "https://www.strava.com/oauth/token"
        activites_url = "https://www.strava.com/api/v3/athlete/activities"


        # Get access token
        print("Requesting Token...\n")
        res = requests.post(auth_url, data=self.codes, verify=False)
        access_token = res.json()['access_token']
        print("Access Token = {}\n".format(access_token))

        # Get activity data
        header = {'Authorization': 'Bearer ' + access_token}
        activity_df_list = []
        for n in range(5):  # TODO: Change this to be higher
            param = {'per_page': 200, 'page': n+1}

            activities_json = requests.get(activites_url, headers=header, params=param).json()
            if not activities_json:
                break
            activity_df_list.append(pd.json_normalize(activities_json))
        activities_df = pd.concat(activity_df_list)
        print('Imported', len(activities_df),'activities')

        return activities_df
    def prep_df(self, activities_df):
            activities_df['polylines'] = activities_df['map.summary_polyline']
            prepped_activities_df = activities_df[['type', 'start_date_local','timezone','polylines']]
            prepped_activities_df = prepped_activities_df.dropna(subset = ['polylines'])
            prepped_activities_df['polylines'] = prepped_activities_df['polylines'].apply(polyline.decode)
            prepped_activities_df = prepped_activities_df.reset_index(drop = True)
            return prepped_activities_df
            

In [393]:
s = StravaAPI('codes.json')
activities_df = s.get_activities()

user_data = s.get_user_data()

Requesting Token...

Access Token = 70d8cc0a0e2cb477d0c6dbd3ac131c7244c2842a

Imported 493 activities
Requesting Token...

Access Token = 70d8cc0a0e2cb477d0c6dbd3ac131c7244c2842a



NotImplementedError: 

In [185]:
prepped_df =s.prep_df(activities_df)
prepped_df

type      start_date_local                      timezone  \
0    Walk  2022-05-22T10:35:56Z   (GMT-05:00) America/Toronto   
1    Walk  2022-05-21T08:59:54Z   (GMT-05:00) America/Toronto   
2    Walk  2022-05-20T16:45:58Z   (GMT-05:00) America/Toronto   
3    Walk  2022-05-19T16:42:08Z   (GMT-05:00) America/Toronto   
4    Walk  2022-05-18T20:52:21Z   (GMT-05:00) America/Toronto   
..    ...                   ...                           ...   
442  Walk  2019-10-04T07:56:50Z   (GMT-05:00) America/Toronto   
443  Walk  2019-10-03T21:25:35Z   (GMT-05:00) America/Toronto   
444  Hike  2019-09-02T09:53:55Z  (GMT-05:00) America/New_York   
445  Hike  2019-08-30T14:31:26Z  (GMT-05:00) America/New_York   
446  Hike  2019-08-26T19:46:16Z  (GMT-05:00) America/New_York   

                                             polylines  
0    [(43.44994, -80.4279), (43.44982, -80.42801), ...  
1    [(43.45033, -80.42919), (43.45057, -80.42947),...  
2    [(43.44976, -80.42824), (43.44977, -80.42826),...  
3    [(43.45051, -80.42944), (43.45057, -80.42939),...  
4    [(43.44986, -80.42761), (43.44986, -80.42764),...  
..                                                 ...  
442  [(43.4729, -80.47299), (43.47285, -80.47287), ...  
443  [(43.45276, -80.43382), (43.45264, -80.43417),...  
444  [(41.82835, -78.99621), (41.82842, -78.99612),...  
445  [(41.76113, -78.58836), (41.76114, -78.58833),...  
446  [(41.48038, -82.68328), (41.48024, -82.6833), ...  

[447 rows x 4 columns]

In [378]:
prepped_df.to_csv('polygons.csv')

In [368]:
from shapely.geometry import Polygon
import folium

def add_polylines(m, polylines, color, opacity = 0.6):
    feature_group = folium.FeatureGroup()
    for line in polylines:
        folium.PolyLine(locations=line, color=color, opacity = opacity).add_to(feature_group)
    feature_group.add_to(m)
def latlong_to_gridcoords(lat, long, width = 0.001):
    """
    Determines the grid point a latitude and longitude would fall in if each grid space had dimensions lat/width and long/width
    
    For 0.001 that means there will be 360000 longitudes and 180000 latitude grid points over the entirety of the globe
    """
    grid_lat = round((lat + 90)/width)
    grid_long = round((long+180)/width)
    return grid_lat, grid_long
    
def gridcoords_to_polygon(grid_lat, grid_long, width = 0.001):
    """
    Turns a grid point, as defined in get_gridcoords() into a square polygon with side length = width
    """
    lat_center = grid_lat*width-90
    long_center = grid_long*width-180
    lats = [lat_center-width/2,lat_center-width/2,lat_center+width/2,lat_center+width/2]
    longs = [long_center-width/2,long_center+width/2,long_center+width/2,long_center-width/2]
    polygon = Polygon(zip(longs,lats)) 
    return polygon

In [376]:
m = folium.Map(tiles='stamentoner', location = [43.45005, -80.42766], zoom_start = 15,prefer_canvas = True) #tiles='OpenStreetMap'
grid_points = {}
for i in range(len(prepped_df['polylines'])):
    for j in range(len(prepped_df['polylines'].iloc[i])):
        lat,long = prepped_df['polylines'].iloc[i][j]
        grid_lat, grid_long = latlong_to_gridcoords(lat,long)
        grid_points[str(grid_lat)+"_"+str(grid_long)] = [grid_lat,grid_long]

feature_group = folium.FeatureGroup()
for key in grid_points.keys():
    grid_lat,grid_long = grid_points[key]
    x = gridcoords_to_polygon(grid_lat,grid_long)
    x2 = x.convex_hull
    folium.GeoJson(x, style_function = lambda x: {'stroke': True, 'color': 'red', 'weight':0.1, 'fillOpacity':0.5}).add_to(feature_group)
feature_group.add_to(m)
# add_polylines(m, prepped_df['polylines'], 'blue')
m
# Next steps are to put this whole system into a nice class and develop a database/storage system to retrieve data
